In [1]:

import pandas as pd
from pathlib import Path
from rl_mind_dataset.common import chat
import os
from dotenv import load_dotenv
import pandas as pd
load_dotenv()
base_path = Path.home() / Path(os.environ.get("DATA_PATH"))
print(base_path)

from tqdm import tqdm


/home/aayush/rsys_data


In [2]:
news_df = pd.read_csv(
    base_path/ Path("news.tsv"), 
    sep="\t",
    names=["news_id","category","subcategory","title","abstract","url","title_entities","abstract_entities"])

In [3]:
valid_behavior = pd.read_csv(
   base_path/ Path("behaviors.tsv"), sep="\t",
    header=None, names=["impression_id", "user_id", "time", "history", "impressions"])
print("Length of valid behavior: ", len(valid_behavior))

Length of valid behavior:  2232748


In [4]:
def get_history_candidate_prompt(behavior):
    history_news = news_df[news_df["news_id"].isin(behavior["history"].split())]
    cand_news_index = [i.split("-")[0] for i in behavior["impressions"].split()]
    cand_label = [i.split("-")[1] for i in behavior["impressions"].split()]
    # get candidate news from news_df and save them to a list with the same order as cand_news_index
    candidate_news = [news_df[news_df["news_id"] == i].iloc[0]["title"] for i in cand_news_index]
    history_prompt = "\n".join([f"H{i + 1}: {news}" for i, news in enumerate(history_news["title"].values)])
    candidate_prompt = "\n".join([f"C{i + 1}: {news}" for i, news in enumerate(candidate_news)])
    return history_prompt, candidate_prompt, ",".join([f"C{i + 1}" for i, l in enumerate(cand_label) if int(l)])

In [5]:
sample100 = pd.read_csv("sampled_100.csv")
imp_recorded = set(sample100["impression_id"].values)
imp_recorded.add(41302)  # one-shot example

In [6]:
len(imp_recorded)

101

In [7]:
sampled_behavior = valid_behavior.sample(36576).index

columns = ["impression_id", "history", "candidate", "label"]
sampled_df = []
sample_num = 1000
for index in sampled_behavior:
    if len(sampled_df) >= sample_num:
        break
    try:
        imp_id = valid_behavior.iloc[index]['impression_id']
        if imp_id in imp_recorded:
            continue
  
        hist, cand, label = get_history_candidate_prompt(valid_behavior.iloc[index])
    
        # print(len(hist.split()), len(cand.split()))
        # if len(hist.split()) > 150 or len(hist.split()) < 50 or len(cand.split()) > 200 or len(cand.split()) < 100:
        #     continue
        # sample behaviors with history and candidate news length between 1000 and 4000
        if len(hist.split()) + len(cand.split()) > 1500 or len(hist.split()) < 10:
            continue
        sampled_df.append([imp_id, hist, cand, label])
        print(len(sampled_df))
    except:
        continue

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [8]:
sampled_df = pd.DataFrame(sampled_df, columns=columns)
print(sampled_df)
for index in tqdm(sampled_df.index, total=len(sampled_df)):
    hist, cand, label = sampled_df.loc[index, ["history", "candidate", "label"]]
    full_prompt = f"""#Input:\nUser's History News:\n{hist}\nCandidate News:\n{cand}\n#Output:"""
    print(full_prompt)
    print(f"Impression ID: {sampled_df.loc[index, 'impression_id']}")

     impression_id                                            history  \
0            53138  H1: 18 major Oscar contender movies you should...   
1           845766  H1: There's a mouse hiding among mushrooms in ...   
2          1986716  H1: Cause determined in Jessi Combs' fatal spe...   
3           954182  H1: 5 Reasons Destin Is a Great Family Vacatio...   
4          1800547  H1: Just in time for Halloween, you can stay o...   
..             ...                                                ...   
995         774422  H1: Road built by biblical villain uncovered i...   
996        1450073  H1: Hunter Biden Steps Down From Chinese Board...   
997        1878254  H1: Doctors Want FDA To Warn Women About Chees...   
998         343653  H1: 'Just trying to have some fun': Nationals'...   
999         925876  H1: New images capture missing college student...   

                                             candidate        label  
0    C1: Broadway Actress Laurel Griggs Dies at Age..

 27%|██▋       | 269/1000 [00:00<00:00, 2688.90it/s]

#Input:
User's History News:
H1: 18 major Oscar contender movies you shouldn't miss in theaters
H2: 31 TV reboots, remakes, and spin-offs that are in the works
H3: Miguel Cervantes' Wife Reveals Daughter, 3, 'Died in My Arms' After Entering Hospice Care
H4: This Artist Reimagined Disney Princesses as Horror Movie Villains, and They're Scary Good
H5: New Movies and TV Shows You'll Be Able to Cozy Up With on Netflix in November
H6: Panera Bread worker fired after TikTok exposed frozen mac and cheese
H7: 'The Little Mermaid Live!': TV Review
Candidate News:
C1: Broadway Actress Laurel Griggs Dies at Age 13
C2: Roommate, her boyfriend charged in death of missing Atlanta student
C3: All eyes on Texas governor as calls grow to halt execution
#Output:
Impression ID: 53138
#Input:
User's History News:
H1: There's a mouse hiding among mushrooms in this viral brainteaser. Can you spot it?
H2: Can you spot the cat hiding among the bats in this spooky Halloween brainteaser?
H3: Can You Find the Gh

 54%|█████▍    | 538/1000 [00:00<00:00, 2212.46it/s]

#Input:
User's History News:
H1: Andy Cohen Says He Doesn't Feel Guilty About Joe and Teresa Giudice's Legal Fate After RHONJ
H2: Joe Giudice 'Feels Like a Weight Has Been Lifted' After ICE Release, Source Says
H3: There's A Black Turtleneck Shortage Because People Are Dressing Up Like Elizabeth Holmes for Halloween
H4: A heartbreaking photo of a dog riding a bus alone went viral, and now people want to adopt her
H5: Model Belle Lucia   Who Was Shamed for Her Small Bump   Shares Her Post-Baby 'Pregnancy Transformation'
H6: Miguel Cervantes' Wife Reveals Daughter, 3, 'Died in My Arms' After Entering Hospice Care
H7: Can you spot the hidden gift in this brainteaser in under 11 seconds?
H8: Former NBA first-round pick Jim Farmer arrested in sex sting operation
H9: Could You Survive the 50 Scariest Haunted House Attractions in the U.S.?
H10: Hillary Clinton blames racism for Meghan Markle's 'inexplicable' treatment by the media
H11: Christopher Dennis Dies: 'Hollywood Superman' And Frequen

100%|██████████| 1000/1000 [00:00<00:00, 1961.63it/s]

#Input:
User's History News:
H1: 'Botched' star spent $174,000 on diamond rings for new bride
Candidate News:
C1: Charles Rogers, former Michigan State football, Detroit Lions star, dead at 38
C2: Rip Taylor's Cause of Death Revealed, Memorial Service Scheduled for Later This Month
#Output:
Impression ID: 1742262
#Input:
User's History News:
H1: Eric Tse, 24, just became a billionaire overnight
H2: Kasich to Congress: 'Look in the mirror at how you want to be remembered'
H3: Joe Biden reportedly denied Communion at a South Carolina church because of his stance on abortion
H4: Jane Fonda, Ted Danson Arrested During Ongoing Climate Change Protest
H5: Milwaukee is the world's hottest new travel destination, according to Airbnb. Here's why it won the top spot.
H6: Fact Checker: Trump's shiny new talking point about income growth
H7: Life expectancy for American men keeps dropping
H8: President Donald Trump greeted with boos at Game 5 of World Series, fans chant 'lock him up'
H9: Chicken re

In [9]:
one_shot = f"""#Input:
User's History News:
H1: Justin Trudeau: no plans 'at all' for a coalition
H2: Soldier wounded searching for Bergdahl dies
H3: Report: Jim Harbaugh exploring potential NFL return
H4: 23 Things You Should Toss from Your Closet Forever
H5: Nick Saban on Donald Trump attending Alabama-LSU: It's an honor he's interested enough to come
H6: McDonald's apologizes for 'Sundae Bloody Sundae' Halloween promotion
H7: Potential Florida State football coaching targets
H8: 9 renovation tips to boost resale value
H9: Former Seminoles star Deion Sanders is not candidate for Florida State football coaching job
H10: Young homebuyers are vanishing from the US
Candidate News:
C1: The Unlikely Star of My Family's Thanksgiving Table
C2: U.S. Troops Will Die If They Remain in Syria, Bashar Al-Assad Warns
C3: 30 Best Black Friday Deals from Costco
C4: Cows swept away by Hurricane Dorian found alive   but how?
C5: Opinion: Colin Kaepernick is about to get what he deserves: a chance
C6: South Carolina teen gets life in prison for deadly elementary school shooting
C7: Report: Police investigating woman's death after Redskins' player Montae Nicholson took her to hospital
C8: 13 Reasons Why's Christian Navarro Slams Disney for Casting 'the White Guy' in The Little Mermaid
C9: Why Teach Your Dog to Sit, When You Can Teach Them to Make a Sandwich Instead?
C10: Some believe Mason Rudolph, hit in head with his own helmet, isn't getting enough blame
C11: Pete Davidson, Kaia Gerber Are Dating, Trying to Stay 'Low Profile'
#Output:C5,C2,C11,C9,C4,C7,C6,C8,C1,C3"""
params = {"max_tokens": 30}
models = ["gpt-3.5-turbo", "gpt-4"]


In [12]:
max_length = 0
count = 0
sampled_df = pd.read_csv("sampled_100.csv")
for index in tqdm(sampled_df.index, total=len(sampled_df)):
    hist, cand, label = sampled_df.loc[index, ["history", "candidate", "label"]]
    full_prompt = f"""You are a news recommender. Given an example like:\n{one_shot}\nNow rank the following input and output up to 10 news index in the format like C1,C4,C2,C3.\n#Input:\nUser's History News:\n{hist}\nCandidate News:\n{cand}\n#Output:"""
    prompt_len = len(full_prompt.split())
    if prompt_len > 1400:
        print(len(hist.split()), len(cand.split()), label)
        count += 1
    # print(len(full_prompt.split()))
    if len(full_prompt.split()) > max_length:
        max_length = len(full_prompt.split())
print(max_length, count)

100%|██████████| 100/100 [00:00<00:00, 1587.96it/s]

918 328 C13,C14
371 880 C20,C32
936 339 C15,C21,C23
725 573 C42
102 1042 C90
947 178 C1
385 802 C4,C5,C18,C21,C30
516 786 C21,C29,C61,C67
1584 8


In [13]:
sampled_df

impression_id                                            history  \
0            1133  H1: Shepard Smith's departure from Fox News co...   
1           22293  H1: Today in History: October 14\nH2: Opinions...   
2           45752  H1: Meghan and Harry to take 'family time' off...   
3           38792  H1: Opinions | Trump is in trouble. Tuesday's ...   
4           69912  H1: Burned in 2008, Americans are refusing to ...   
..            ...                                                ...   
95          71330  H1: Why you should take the stairs at the Eiff...   
96          13701  H1: Emily Ratajkowski Is Being Sued for $150,0...   
97          12000  H1: TV reporter fired after climbing on cars l...   
98          25533  H1: Joe Biden reportedly denied Communion at a...   
99          38923  H1: How these 4 kids searched for   and found ...   

                                            candidate            label  
0   C1: Today in History: November 15\nC2: 'This t...          C13,C14  
1   C1: Meghan Markle and Hillary Clinton Secretly...            C1,C7  
2   C1: The most talked about movie moments of the...      C17,C25,C29  
3   C1: University of Florida student president fa...           C6,C10  
4   C1: Former North Carolina State, NBA player An...            C1,C6  
..                                                ...              ...  
95  C1: Taylor Swift Rep Hits Back at Big Machine,...              C10  
96  C1: Amari gets heroic birthday surprise\nC2: T...  C21,C29,C61,C67  
97  C1: 2019 Los Angeles Auto Show Preview\nC2: At...              C23  
98  C1: How much turkey do you need to buy per per...              C19  
99  C1: The most talked about movie moments of the...              C18  

[100 rows x 4 columns]